In [1]:
import nltk

In [2]:
corpus = nltk.corpus.gutenberg.sents(u'austen-emma.txt')

# Get unigrams and Bigrams

In [4]:
def get_unigrams(corpus):
    unigrams = {}
    for sentence in corpus:
        for word in sentence:
            word = word.lower()
            if word not in unigrams:
                unigrams[word] = 0
            unigrams[word] += 1
    return unigrams

def sort_dict(d, reverse = True):
    return sorted(d.items(), key = lambda x : x[1], reverse = reverse)

In [5]:
from ipy_table import *

In [6]:
unigrams = get_unigrams(corpus)
sorted_unigrams = sort_dict(unigrams)

In [7]:
make_table(sorted_unigrams)

In [57]:
from plotly import __version__
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
from plotly.graph_objs import *
init_notebook_mode(connected=True)
iplot([{"x" : list(zip(*sorted_unigrams))[0], "y": list(zip(*sorted_unigrams))[1]}])

In [9]:
import math
def unigram_probs(unigrams):
    new_unigrams = {}
    N = sum(unigrams.values())
    for word in unigrams:
        new_unigrams[word] =  round(unigrams[word] / float(N), 15)
        #new_unigrams[word] =  math.log(unigrams[word] / float(N))
    return new_unigrams
    

In [10]:
uprobs = unigram_probs(unigrams)
sorted_uprobs = sort_dict(uprobs)
make_table(sorted_uprobs)

In [58]:
iplot([{"x" : list(zip(*sorted_uprobs))[0], "y": list(zip(*sorted_uprobs))[1]}])
#iplot([{"x" : [math.log(i+1) for i in range(len(sorted_uprobs))], "y": list(zip(*sorted_uprobs))[1]}])

# Add-One Smoothing

In [14]:
def add_one(unigrams,V):
    new_unigrams = {}
    N = sum(unigrams.values())
    for word in unigrams:
        new_unigrams[word] = round((unigrams[word] + 1)/ float(N+V), 15) * N
        #new_unigrams[word] = math.log((unigrams[word] + 1)/ float(N+V))
    return new_unigrams


In [59]:
smoothed_200 = sort_dict(add_one(unigrams, 200))
smoothed_2000 = sort_dict(add_one(unigrams, 2000))
smoothed_double = sort_dict(add_one(unigrams, len(unigrams)*10))



#p1 = Scatter(x = list(zip(*sorted_uprobs))[0], y= list(zip(*sorted_uprobs))[1], mode='lines', name="unsmoothed")
p1 = Scatter(x = list(zip(*sorted_uprobs))[0], y= list(zip(*sorted_unigrams))[1], mode='lines', name="unsmoothed")
p2 = Scatter(x = list(zip(*smoothed_200))[0], y= list(zip(*smoothed_200))[1], mode='lines', name="200")
p3 = Scatter(x = list(zip(*smoothed_2000))[0], y= list(zip(*smoothed_2000))[1], mode='lines', name="2000")
p4 = Scatter(x = list(zip(*smoothed_double))[0], y= list(zip(*smoothed_double))[1], mode='lines', name="double")
iplot([p1, p2, p3, p4])

In [17]:
def get_bigrams(corpus):
    bigrams = {}
    for sentence in corpus:
        for index, word in enumerate(sentence):
            if index > 0:                
                word = word.lower()            
                prev = sentence[index - 1].lower()
                if prev not in bigrams:
                    bigrams[prev] = {}
                if word not in bigrams[prev]:
                    bigrams[prev][word]  = 0
                bigrams[prev][word] += 1
    return bigrams

In [60]:
bigrams = get_bigrams(corpus)
bg_word = sort_dict(unigram_probs(bigrams['kind']))
p1 = Scatter(x = list(zip(*bg_word))[0], y = list(zip(*bg_word))[1], name='unsmoothed')
bg_smoothed = sort_dict(add_one(bigrams['kind'], len(unigrams)))
p2 = Scatter(x = list(zip(*bg_smoothed))[0], y = list(zip(*bg_smoothed))[1], name='smoothed')
iplot([p1,p2])

# Heldout Smoothing

In [19]:
#Heldout
training = corpus[:5000]
heldout = corpus[5000:]

In [20]:
utraining = get_unigrams(training)
uheldout = get_unigrams(heldout)

In [21]:
def eq_classes(ugrams):
    eq = {}
    for k, v in ugrams.items():
        if v not in eq:
            eq[v] = []
        eq[v].append(k)
    return eq

In [22]:
tr_eq_cls = eq_classes(utraining)
for r in tr_eq_cls:
    print(r, tr_eq_cls[r])


1 ['concise', 'offered', 'purse', 'persuasions', 'excess', 'reception', 'partake', 'descried', 'sobering', 'commandingly', 'inexperience', 'shared', 'pitiable', 'elbow', 'slept', 'twisted', 'contributing', 'knife', 'career', 'verified', 'salting', 'gala', 'rejection', 'studied', 'pangs', 'troubles', 'scalloped', 'unfrequently', 'deposited', 'bench', 'extricated', 'profusion', 'weakened', 'envy', 'explain', 'encourager', 'bashfulness', 'wretches', 'gainer', 'tyrannic', 'measures', 'perpetual', 'permanent', 'variation', 'encouragements', 'disorder', 'politician', 'plea', 'pitifullest', 'detached', 'incredible', 'courtesies', 'vouchsafed', 'exterior', 'completest', 'insulted', 'learned', 'shrinking', 'provocation', 'shilling', 'selves', 'dwelling', 'prime', 'contingencies', 'gloried', 'puzzles', 'compressed', 'dews', 'brighter', 'hereafter', 'moral', 'smartened', 'dumpling', 'coddling', 'produces', 'alphabetically', 'finale', 'pardoned', 'outcry', 'untouched', 'porker', 'taller', 'overcom

In [23]:
def get_heldout(hugrams, eq):
    hest = {}
    for r in eq:
        t_r = sum([hugrams[u] for u in eq[r] if u in hugrams])
        hest[r] = t_r
    return hest

In [63]:
hestimate = get_heldout(uheldout, tr_eq_cls)
N = sum(list(utraining.values()))
new_estimates = []
old_estimates = []
for r, t_r in sorted(hestimate.items()):
    new_estimates +=  [t_r/(len(tr_eq_cls[r])*N)]
    old_estimates += [r/N]
    print(r, len(tr_eq_cls[r]), hestimate[r], hestimate[r]/len(tr_eq_cls[r]), hestimate[r]/(len(tr_eq_cls[r]) * N), r/N)

1 2467 1131 0.45845156059991893 3.782260360857669e-06 8.250076313205898e-06
2 929 969 1.0430570505920345 8.605300266411749e-06 1.6500152626411795e-05
3 487 736 1.51129363449692 1.246828781626189e-05 2.4750228939617693e-05
4 298 606 2.033557046979866 1.6777000824841523e-05 3.300030525282359e-05
5 248 653 2.6330645161290325 2.1722983195659077e-05 4.1250381566029484e-05
6 180 666 3.7 3.052528235886182e-05 4.9500457879235385e-05
7 144 547 3.798611111111111 3.133883155085851e-05 5.775053419244128e-05
8 118 490 4.1525423728813555 3.425879147009229e-05 6.600061050564718e-05
9 87 409 4.7011494252873565 3.878484151840474e-05 7.425068681885307e-05
10 62 414 6.67741935483871 5.508921925269744e-05 8.250076313205897e-05
11 65 376 5.7846153846153845 4.7723518365621806e-05 9.075083944526487e-05
12 56 371 6.625 5.465675557498907e-05 9.900091575847077e-05
13 40 249 6.225 5.135672504970671e-05 0.00010725099207167666
14 28 195 6.964285714285714 5.7455888609826785e-05 0.00011550106838488256
15 36 401 11.1

652 1 379 379.0 0.003126778922705035 0.005379049756210245
658 1 316 316.0 0.0026070241149730635 0.00542855021408948
746 1 471 471.0 0.0038857859435199775 0.006154556929651599
761 1 384 384.0 0.0031680293042710647 0.006278308074349688
768 1 385 385.0 0.0031762793805842704 0.006336058608542129
786 1 371 371.0 0.003060778312199388 0.006484559982179835
825 1 495 495.0 0.004083787775036919 0.006806312958394865
827 1 375 375.0 0.0030937786174522115 0.006822813111021277
828 1 609 609.0 0.005024296474742391 0.006831063187334483
866 1 481 481.0 0.003968286706652037 0.007144566087236307
879 1 361 361.0 0.002978277549067329 0.007251817079307984
926 1 698 698.0 0.005758553266617716 0.007639570666028661
927 1 509 509.0 0.004199288843421802 0.007647820742341866
953 1 488 488.0 0.004026037240844478 0.00786232272648522
1098 1 708 708.0 0.005841054029749776 0.009058583791900075
1140 1 666 666.0 0.005494550824595127 0.009405086997054724
1193 1 787 787.0 0.006492810058493041 0.009842341041654636
1251 1 7

In [64]:
p1 = Bar(x = list(hestimate.keys()), y = old_estimates, name='unsmoothed')
p2 = Bar(x = list(hestimate.keys()) , y = new_estimates, name='smoothed')
iplot([p1,p2])

# Good Turing

In [66]:
nrs = eq_classes(unigrams)
nr_counts = {k : len(v) for k, v in nrs.items()}
nr_probs = {k : (k*v)/float(N) for k, v in nr_counts.items()} # P = r * Nr / N
sorted_nrs = sorted(nr_counts.items())
sorted_probs = sorted(nr_probs.items())
nr_counts

{1: 2888,
 2: 1062,
 3: 575,
 4: 430,
 5: 310,
 6: 202,
 7: 161,
 8: 139,
 9: 114,
 10: 110,
 11: 99,
 12: 82,
 13: 67,
 14: 57,
 15: 40,
 16: 45,
 17: 41,
 18: 31,
 19: 38,
 20: 31,
 21: 28,
 22: 24,
 23: 26,
 24: 25,
 25: 22,
 26: 20,
 27: 21,
 28: 14,
 29: 15,
 30: 12,
 31: 26,
 32: 14,
 33: 11,
 34: 9,
 35: 9,
 36: 12,
 37: 6,
 38: 14,
 39: 16,
 40: 12,
 41: 10,
 42: 9,
 43: 6,
 44: 6,
 45: 7,
 46: 10,
 47: 8,
 48: 8,
 49: 5,
 50: 6,
 51: 9,
 52: 5,
 53: 5,
 54: 4,
 55: 5,
 56: 9,
 57: 4,
 58: 3,
 59: 8,
 60: 6,
 61: 5,
 62: 3,
 63: 5,
 64: 8,
 65: 4,
 66: 8,
 67: 4,
 68: 5,
 69: 3,
 70: 5,
 71: 3,
 72: 3,
 73: 6,
 75: 3,
 76: 3,
 77: 3,
 78: 1,
 79: 1,
 80: 4,
 81: 4,
 82: 2,
 83: 2,
 84: 1,
 85: 5,
 86: 1,
 87: 2,
 88: 3,
 89: 3,
 90: 4,
 91: 2,
 92: 3,
 93: 1,
 94: 1,
 95: 5,
 96: 2,
 97: 3,
 98: 1,
 99: 3,
 100: 2,
 101: 1,
 102: 4,
 103: 1,
 106: 1,
 108: 1,
 109: 2,
 111: 1,
 112: 1,
 113: 2,
 114: 1,
 115: 2,
 117: 2,
 118: 1,
 119: 3,
 120: 3,
 121: 1,
 122: 1,
 124: 1,
 12

In [69]:
MAX = sorted_nrs[0][1]
# R vs NR
iplot([
    Bar({"x" : list(zip(*sorted_nrs))[0], "y": list(zip(*sorted_nrs))[1]}, name="original"),    
    Bar({"x" : list(zip(*sorted_nrs))[0], "y": [(MAX)*(x[0]**-2) for x in sorted_nrs]}, name="aR^b") # ab^r
])
# R vs Probability Mass of R
regress_probs = sorted({k : (MAX*k**-2)/float(N) for k, v in nr_counts.items()}.items())
iplot([
    Bar({"x" : list(zip(*sorted_probs))[0], "y": list(zip(*sorted_probs))[1]}, name="original"),    
    Bar({"x" : list(zip(*regress_probs))[0], "y": list(zip(*regress_probs))[1]}, name="aR^b"), # ab^r
])
# Ps. Zoom to see the bars. 

In [71]:
def good_turing(nrs):
    new_nrs = {}
    for r, nr in nrs.items():
        if (r+1) in nrs:
            new_nr = ((r+1) * nrs[r+1]) / float(N) 
        else:
            new_nr = MAX*r**-2 / float(N)
        new_nrs[r] = new_nr
    return new_nrs

In [72]:
new_nrs = good_turing(nr_counts)
sorted_newnrs = sorted(new_nrs.items())
sorted_newnrs

[(1, 0.017523162089249325),
 (2, 0.014231381640280172),
 (3, 0.014190131258714144),
 (4, 0.01278761828546914),
 (5, 0.009999092491605547),
 (6, 0.009297836004983046),
 (7, 0.009174084860284957),
 (8, 0.00846457829734925),
 (9, 0.009075083944526488),
 (10, 0.008984333105081222),
 (11, 0.008118075092194603),
 (12, 0.007185816468802337),
 (13, 0.006583560897938306),
 (14, 0.004950045787923538),
 (15, 0.005940054945508246),
 (16, 0.00575030319030451),
 (17, 0.004603542582768891),
 (18, 0.005956555098134658),
 (19, 0.005115047314187656),
 (20, 0.004851044872165067),
 (21, 0.0043560402933727135),
 (22, 0.004933545635297127),
 (23, 0.004950045787923538),
 (24, 0.004537541972263244),
 (25, 0.0042900396828670665),
 (26, 0.004677793269587744),
 (27, 0.0032340299147767117),
 (28, 0.003588783196244565),
 (29, 0.002970027472754123),
 (30, 0.006649561508443953),
 (31, 0.003696034188316242),
 (32, 0.0029947777016937406),
 (33, 0.0025245233518410046),
 (34, 0.0025987740386598577),
 (35, 0.003564032967

In [73]:

iplot([
    Bar({"x" : list(zip(*sorted_probs))[0], "y": list(zip(*sorted_probs))[1]}, name="original"),
    Bar({"x" : list(zip(*sorted_newnrs))[0], "y": list(zip(*sorted_newnrs))[1]}, name="good-turing"),
     Bar({"x" : list(zip(*regress_probs))[0], "y": list(zip(*regress_probs))[1]}, name="aR^b"), # ab^r

])

# Kneser-Ney

In [74]:
def witten_bell(w, bigrams, unigrams):
    
    #wb_lambda = get_lambdaval(prior, text)
    #new_prior = ' '.join(prior.split()[:-1])
    #wb_prob = (1-wb_lambda)*laplace_mle(lik, prior, text) + wb_lambda*witten_bell(lik, new_prior, text)
    wprobs = {}
    prior_count = sum(list(bigrams[w].values()))
    type_count = len(list(bigrams[w].keys()))
    bprobs = {}
    for b in bigrams[w]:
        ngram_count = bigrams[w][b] / float(prior_count)
        bprobs[b]= ngram_count
        #vocab_size = len(get_vocab(text))
        wblambda = type_count / float(type_count + prior_count)
        wb_prob = (1-wblambda)*ngram_count + wblambda*unigrams[w]
        #print(unigrams[w])
        wprobs[b] = wb_prob
    return bprobs, wprobs
    #z = vocab_size - type_count
    #if ngram_count == 0:
    #    wb_prob = float(type_count)/float(z*(prior_count + type_count))
    #else:
    #    wb_prob = float(ngram_count)/float(prior_count + type_count)
    #return wb_prob

In [76]:
bprobs, wprobs = witten_bell('good', bigrams, uprobs)
sorted_bprobs = sort_dict(bprobs)
sorted_wprobs = sort_dict(wprobs)

iplot([
    Scatter({"x" : list(zip(*sorted_bprobs))[0], "y": list(zip(*sorted_bprobs))[1]}, name="original"),
    Scatter({"x" : list(zip(*sorted_wprobs))[0], "y": list(zip(*sorted_wprobs))[1]}, name="wittenbell"),
     

])